In [1]:
import os
import pandas as pd
import numpy as np
import requests
from bs4 import BeautifulSoup
import random
from pprint import *

# Set the URL to scrape
url = "https://en.wikipedia.org/wiki/List_of_airports_in_the_United_States"

# Define a filename for the HTML file to be saved
filename = "Wikipedia_Airports"

# Check if the file has been saved already today
if os.path.exists(filename):
    print("I have a file!")
    # If the file exists, open it and read its contents into the html variable
    with open(filename, "r") as f:
        html = f.read()
else:
    # If the file doesn't exist, scrape the URL and save the HTML file
    response = requests.get(url)
    print("I'm scraping!")
    html = response.text
    with open(filename, "w") as f:
        f.write(html)

# Parse the HTML using BeautifulSoup
soup = BeautifulSoup(html, "html.parser")

# Find all the tables in the HTML
tables = soup.find_all("table")

# Load each table into a pandas data frame
dfs = []
for table in tables:
    # Convert the table HTML to a pandas dataframe and append it to the list of dataframes
    df = pd.read_html(str(table))[0]
    dfs.append(df)
print(f"{len(dfs)} tables found.")
if len(dfs) == 1:
    # If only one table was found, use that as the dataframe
    df = dfs[0]

I have a file!
4 tables found.


In [2]:
# Get the third table from the list of dataframes
airports = dfs[2]

# Add a new column called "State" and fill it with NaN values
airports["State"] = np.nan

# Loop through each row in the airports dataframe
for index,row in airports.iterrows():
    # Check if the "Airport" column for the current row is NaN
    airports_nan = airports.isna()
    if airports_nan.loc[index,"Airport"] == True:
        # If it is NaN, set the "state" variable to the value in the "City" column for the current row
        state = airports.loc[index,"City"]
    else:
        # If it is not NaN, set the "State" column for the current row to the "state" variable
        airports.loc[index,"State"] = str(state.title())

# Drop any rows where the "Airport" column is NaN
airports.dropna(subset=["Airport"],inplace=True)

# Print the first five rows of the dataframe
airports.head()

City  FAA IATA  ICAO  \
1  Birmingham  BHM  BHM  KBHM   
2      Dothan  DHN  DHN  KDHN   
3  Huntsville  HSV  HSV  KHSV   
4      Mobile  MOB  MOB  KMOB   
5  Montgomery  MGM  MGM  KMGM   

                                             Airport Role  Enplanements  \
1     Birmingham–Shuttlesworth International Airport  P-S     1081328.0   
2                            Dothan Regional Airport  P-N       37047.0   
3  Huntsville International Airport (Carl T. Jone...  P-S      459759.0   
4                            Mobile Regional Airport  P-N      236007.0   
5       Montgomery Regional Airport (Dannelly Field)  P-N      129033.0   

     State  
1  Alabama  
2  Alabama  
3  Alabama  
4  Alabama  
5  Alabama

In [3]:
# Read in the "us-airports.csv" file as a pandas dataframe
us_airports = pd.read_csv('us-airports.csv')

# Merge the "airports" and "us_airports" dataframes using the "ICAO" column in "airports" and the "ident" column in "us_airports"
all_airports = pd.merge(airports, us_airports, left_on='ICAO', right_on='ident')

# Drop the "ident" column from the merged dataframe
all_airports.drop('ident', axis=1, inplace=True)

# Delete the "airports" and "us_airports" dataframes to free up memory
del(airports)
del(us_airports)

# Capitalize the first letter of each column name in the merged dataframe
all_airports.columns = all_airports.columns.str.title()
all_airports.drop(all_airports[all_airports['State']== 'Alaska'].index, inplace=True)
all_airports.drop(all_airports[all_airports['State']== 'Hawaii'].index, inplace=True)
# Rename the "Faa", "Iata", and "Icao" columns to "FAA", "IATA", and "ICAO", respectively
all_airports.rename(columns={"Faa":"FAA","Iata":"IATA","Icao":"ICAO"},inplace=True)

# Print the first five rows of the merged dataframe
all_airports.head()

City  FAA IATA  ICAO  \
0  Birmingham  BHM  BHM  KBHM   
1      Dothan  DHN  DHN  KDHN   
2  Huntsville  HSV  HSV  KHSV   
3      Mobile  MOB  MOB  KMOB   
4  Montgomery  MGM  MGM  KMGM   

                                             Airport Role  Enplanements  \
0     Birmingham–Shuttlesworth International Airport  P-S     1081328.0   
1                            Dothan Regional Airport  P-N       37047.0   
2  Huntsville International Airport (Carl T. Jone...  P-S      459759.0   
3                            Mobile Regional Airport  P-N      236007.0   
4       Montgomery Regional Airport (Dannelly Field)  P-N      129033.0   

     State    Id            Type  ... Municipality Scheduled_Service Gps_Code  \
0  Alabama  3406  medium_airport  ...   Birmingham                 1     KBHM   
1  Alabama  3489  medium_airport  ...       Dothan                 1     KDHN   
2  Alabama  3594  medium_airport  ...   Huntsville                 1     KHSV   
3  Alabama  3700  medium_airport  ...       Mobile                 1     KMOB   
4  Alabama  3681  medium_airport  ...   Montgomery                 1     KMGM   

  Iata_Code Local_Code                                          Home_Link  \
0       BHM        BHM                      http://www.flybirmingham.com/   
1       DHN        DHN                                                NaN   
2       HSV        HSV  http://www.flyhuntsville.com/portal/#.VbaG-_lVhBc   
3       MOB        MOB                         http://www.mobairport.com/   
4       MGM        MGM                             http://www.flymgm.com/   

                                      Wikipedia_Link Keywords Score  \
0  https://en.wikipedia.org/wiki/Birmingham_Inter...      NaN   750   
1  https://en.wikipedia.org/wiki/Dothan_Regional_...      NaN   750   
2  https://en.wikipedia.org/wiki/Huntsville_Inter...      NaN   750   
3  https://en.wikipedia.org/wiki/Mobile_Regional_...      NaN   750   
4  https://en.wikipedia.org/wiki/Montgomery_Regio...      NaN   750   

                Last_Updated  
0  2021-11-21T15:02:17+00:00  
1  2008-06-13T14:30:04+00:00  
2  2021-11-21T15:08:07+00:00  
3  2021-11-20T15:04:45+00:00  
4  2022-10-13T12:15:15+00:00  

[5 rows x 30 columns]

In [4]:
class Airport:
    def __init__(self, row):
        for col in row.index:
            setattr(self, col, row[col])
            
    def __repr__(self):
        return f"Airport({self.ICAO})" # Returns a string representation of the Airport object
        
    def __str__(self):
        return f"{self.ICAO}" # Returns a string representation of the Airport object
    
    Airport_List = [] # A list to store Airport objects

In [5]:
for _, row in all_airports.iterrows():
    Airport.Airport_List.append(Airport(row)) # Create Airport objects and add them to Airport_List
    
pprint(Airport.Airport_List) # Pretty-print the list of Airport objects

[Airport(KBHM),
 Airport(KDHN),
 Airport(KHSV),
 Airport(KMOB),
 Airport(KMGM),
 Airport(KFLG),
 Airport(KIWA),
 Airport(KPGA),
 Airport(KPHX),
 Airport(KPRC),
 Airport(KTUS),
 Airport(KNYL),
 Airport(KXNA),
 Airport(KFSM),
 Airport(KLIT),
 Airport(KTXK),
 Airport(KACV),
 Airport(KBFL),
 Airport(KBUR),
 Airport(KFAT),
 Airport(KLGB),
 Airport(KLAX),
 Airport(KMRY),
 Airport(KOAK),
 Airport(KONT),
 Airport(KSNA),
 Airport(KPSP),
 Airport(KRDD),
 Airport(KSMF),
 Airport(KSAN),
 Airport(KSFO),
 Airport(KSJC),
 Airport(KSBP),
 Airport(KSBA),
 Airport(KSMX),
 Airport(KSTS),
 Airport(KSCK),
 Airport(KALS),
 Airport(KASE),
 Airport(KCOS),
 Airport(KDEN),
 Airport(KDRO),
 Airport(KEGE),
 Airport(KGJT),
 Airport(KGUC),
 Airport(KHDN),
 Airport(KMTJ),
 Airport(KBDL),
 Airport(KHVN),
 Airport(KILG),
 Airport(KDAB),
 Airport(KFLL),
 Airport(KRSW),
 Airport(KVPS),
 Airport(KGNV),
 Airport(KJAX),
 Airport(KEYW),
 Airport(KMLB),
 Airport(KMIA),
 Airport(KMCO),
 Airport(KECP),
 Airport(KPNS),
 Airport

In [6]:
class Route:
    def __init__(self, origin, destination):
        self.origin = origin
        self.destination = destination
    
    def __repr__(self):
        return f"Route({self.origin.ICAO} -> {self.destination.ICAO})"
        
    def __str__(self):
        return f"{self.origin.ICAO} -> {self.destination.ICAO}"

def create_random_route_network(num_routes, hubs=None):
    if hubs is None:
        hubs = []

    # Convert the enplanements to a logistic distribution for weighting
    weights = np.logistic(0, 100000, size=len(Airport.Airport_List))

    # Get a list of possible origin airports
    origin_list = [airport for airport in Airport.Airport_List if airport.ICAO not in hubs]

    routes = []

    while len(routes) < num_routes:
        # Select a random origin airport based on weights
        origin = random.choices(origin_list, weights=weights)[0]

        # Get a list of possible destination airports
        dest_list = [airport for airport in Airport.Airport_List if airport.ICAO not in hubs and airport != origin]

        # Select a random destination airport based on weights
        destination = random.choices(dest_list, weights=weights)[0]

        # Check if the origin and destination airports have at least one other route
        if (len(origin.routes) > 1 or len(dest.routes) > 1) and origin != destination:
            # Create the route
            route = Route(origin, destination)
            routes.append(route)
            origin.routes.append(route)
            dest.routes.append(route)

    # Check for isolated routes and repeat until there are none
    while True:
        isolated_routes = []
        for airport in Airport.Airport_List:
            if len(airport.routes) == 1:
                isolated_routes.append(airport.routes[0])

        if len(isolated_routes) == 0:
            break

        for route in isolated_routes:
            origin = route.origin
            dest = route.destination
            origin.routes.remove(route)
            dest.routes.remove(route)
            routes.remove(route)

        while len(routes) < num_routes:
            origin = random.choices(origin_list, weights=weights)[0]
            dest_list = [airport for airport in Airport.Airport_List if airport.ICAO not in hubs and airport != origin]
            destination = random.choices(dest_list, weights=weights)[0]
            if (len(origin.routes) > 1 or len(dest.routes) > 1) and origin != destination:
                route = Route(origin, destination)
                routes.append(route)
                origin.routes.append(route)
                dest.routes.append(route)

    return routes

In [7]:
from scipy.special import expit

def stretch_list(numbers):
    # Find the minimum and maximum values
    min_value = min(numbers)
    max_value = max(numbers)

    # Stretch the values between 1 and 100
    stretched = []
    for value in numbers:
        stretched_value = ((value - min_value) / (max_value - min_value)) * 99 + 1
        stretched.append(stretched_value)

    return stretched

# Get enplanements for all airports
enplanements = [airport.Enplanements for airport in Airport.Airport_List]

# Normalize enplanements to a logistic curve
enplanements_logistic = expit((enplanements - np.mean(enplanements)) / np.std(enplanements))

# Assign Weight attribute to each airport based on enplanements
for i, airport in enumerate(Airport.Airport_List):
    airport.Weight = enplanements_logistic[i]
    
# create empty dictionary to store weights
weights_dict = {}

# iterate over the list of airports
for airport in Airport.Airport_List:
    # add airport and its weight to the dictionary
    weights_dict[airport.ICAO] = airport.Weight**2

In [8]:
class Route:
    def __init__(self, origin, destination):
        self.origin = origin
        self.destination = destination
        self.isolated = False

    def __repr__(self):
        return f"Route({self.origin}-{self.destination})"

In [9]:
def search_ICAO(icao_code):
    for airport in Airport.Airport_List:
        if airport.ICAO == icao_code:
            return airport
    return None

In [10]:
def create_random_route_network(num_routes, hubs=None, hub_modifier=150, selection_modifier=200):
    """
    Creates a random route network for an airline.

    Parameters:
    num_routes (int): Number of routes to create.
    hubs (list of str, optional): List of ICAO code strings representing hubs.
    
    Returns:
    list of Route: List of randomly generated routes.
    """
    if hubs is None:
        hubs = []
        
    weights = weights_dict.copy()
    
    for hub in hubs:
        weights[hub] = weights[hub]*hub_modifier
    
    airport_list = [airport.ICAO for airport in Airport.Airport_List]
    route_list = []
    
    while len(route_list) < num_routes:
        weights_list = stretch_list(list(weights.values()))
        origin = random.choices(airport_list, weights_list)[0]
        destination = origin
        while destination == origin:
            destination = random.choices(airport_list, weights_list)[0]

        route_list.append(Route(origin, destination))
        weights[origin] = weights[origin]+selection_modifier
        weights[destination] = weights[destination]+selection_modifier
        
    origins = [route.origin for route in route_list]
    destinations = [route.destination for route in route_list]
    cities = origins+destinations
    counts = dict(Counter(cities))
    isolated = []
    for city, count in counts.items():
        if count == 1:
            isolated.append(city)
            
    for route in route_list:
        if (route.origin in isolated) and (route.destination in isolated):
            route_list.remove(route)

    print(f"Generated {len(route_list)} routes.")
    return route_list

In [11]:
import geopandas as gpd
from shapely.geometry import Point, LineString
import matplotlib.pyplot as plt

def plot_route_map(routes):
    # Create GeoDataFrame with airport locations
    airports = gpd.GeoDataFrame(
        [(a.ICAO, Point(float(a.Longitude_Deg), float(a.Latitude_Deg))) for a in Airport.Airport_List],
        columns=['ICAO', 'geometry'],
        crs='EPSG:4326'
    )

    # Create GeoDataFrame with route geometries
    route_geoms = []
    for route in routes:
        start_airport = search_ICAO(route.origin)
        end_airport = search_ICAO(route.destination)
        route_geom = LineString([(float(start_airport.Longitude_Deg),float(start_airport.Latitude_Deg)),
                                 (float(end_airport.Longitude_Deg), float(end_airport.Latitude_Deg))])
        route_geoms.append(route_geom)
    routes_gdf = gpd.GeoDataFrame(geometry=route_geoms, crs='EPSG:4326')

    # Add country borders
    us = gpd.read_file("States_shapefile.shp")

    # Set plot resolution
    fig, ax = plt.subplots(figsize=(16, 9), dpi=1000)

    # Plot the GeoDataFrames with different colors and sizes
    us.plot(ax=ax, color='white', edgecolor='black', alpha=0.5, linewidth=0.5)
    airports.plot(ax=ax, marker='o', markersize=1.5, color='navy', alpha=0.5)
    routes_gdf.plot(ax=ax, color='navy', linewidth=0.15)

    for i, row in airports.iterrows():
        ax.annotate(text=row['ICAO'], xy=row.geometry.centroid.coords[0], ha='center', fontsize=4)
    # Set axis labels and title
    ax.set_title("Routes and Airports in the US")
    ax.set_xlabel("Longitude")
    ax.set_ylabel("Latitude")
    ax.set_xlim(-130,-65)
    ax.set_ylim(24,50)
    
    # Show the plot
    plt.show()
    
    ax.set_xlim(-180,-125)
    ax.set_ylim(50,75)
    plt.show()
    
    ax.set_xlim(-165,-150)
    ax.set_ylim(18,23)
    plt.show()

In [12]:
from collections import Counter


# origins = [route.origin for route in routes]
# destinations = [route.destination for route in routes]
# cities = origins+destinations

# counts = Counter(cities)
# pprint(counts)

In [17]:
routes = create_random_route_network(10, hubs = ['KORD','KBIL','KASE','KFAR','KOMA','KSEA'],hub_modifier=3500,selection_modifier=10)
plot_route_map(routes)

Generated 7 routes.


In [14]:
origins = [route.origin for route in routes]
destinations = [route.destination for route in routes]
cities = origins+destinations

counts = dict(Counter(cities))
new = {}
for key,val in counts.items():
    new[search_ICAO(key).Name]=val
pprint(new)

{'Appleton International Airport': 1,
 'Aspen-Pitkin County Airport (Sardy Field)': 3,
 'Austin Straubel International Airport': 1,
 'Bert Mooney Airport': 2,
 'Billings Logan International Airport': 7,
 'Bishop International Airport': 2,
 'Block Island State Airport': 3,
 'Boeing Field King County International Airport': 1,
 'California Redwood Coast-Humboldt County Airport': 1,
 'Capital City Airport': 3,
 'Casper-Natrona County International Airport': 2,
 'Charlotte County Airport': 3,
 'Charlottesville Albemarle Airport': 8,
 "Chicago O'Hare International Airport": 27,
 'Chippewa County International Airport': 1,
 'City of Colorado Springs Municipal Airport': 1,
 'Coastal Carolina Regional Airport': 1,
 'Columbia Regional Airport': 1,
 'Dallas Fort Worth International Airport': 1,
 'Dothan Regional Airport': 1,
 'Elko Regional Airport': 1,
 'Eppley Airfield': 5,
 'Fort Smith Regional Airport': 4,
 'George Bush Intercontinental Houston Airport': 1,
 'Gerald R. Ford International Air